In [14]:
import numpy as np
import math
import copy

gamma = 0.4
N_e = 30

In [15]:
class State:
    ball_x = 0
    ball_y = 0
    velocity_x = 0
    velocity_y = 0
    paddle_y = 0
    terminate = False
    
    
    def print_state(self):
        print(np.around(self.ball_x, 2) , " " , np.around(self.ball_y, 2) , " " ,  
              np.around(self.velocity_x, 2) , " " ,  np.around(self.velocity_y, 2) , " " ,  np.around(self.paddle_y, 2))
              
 
    def __init__(self, bx, by, vx, vy, p):
        self.ball_x = bx
        self.ball_y = by
        self.velocity_x = vx
        self.velocity_y = vy
        self.paddle_y = p
        
         
    def up(self):
        self.paddle_y = max(self.paddle_y - 0.04, 0)
        
        self.update()
        #print("in function up", match(self))

    def down(self):
        self.paddle_y = min(self.paddle_y + 0.04, 0.8)
        self.update()

    def update(self):
        global num_bounce
#         global state_tracker
        
        self.ball_x += self.velocity_x
        self.ball_y += self.velocity_y
        
        if self.ball_x >= 1:        # hitting right bound
            
            
            if self.ball_y >= self.paddle_y and self.ball_y <= self.paddle_y + 0.2:    # hitting paddle
                self.ball_x = 2 - self.ball_x
                #print("bounce")
                num_bounce += 1
#                 if curr_state not in state_tracker:
#                     #print(curr_state)
#                     state_tracker.append(curr_state)
                                
                self.velocity_x = -self.velocity_x + np.random.uniform(-0.015, 0.015)
                if self.velocity_x < 0:
                    self.velocity_x = min(-0.03, self.velocity_x)
                else:
                    self.velocity_x = max(0.03, self.velocity_x)
                if self.velocity_x > 1:
                    self.velocity_x = 1
                elif self.velocity_x < -1:
                    self.velocity_x = -1
                
                self.velocity_y += np.random.uniform(-0.03, 0.03)
                if self.velocity_y > 1:
                    self.velocity_y = 1
                elif self.velocity_y < -1:
                    self.velocity_y = -1
                    
                
                state_tracker = []
                
            else:    # missing paddle
                #print("terminate")
                self.ball_x = 2 - self.ball_x
#                 reward(state_tracker,-1)
#                 state_tracker = []
                self.terminate = True

            
        if self.ball_x <= 0:     # hitting left bound
            self.ball_x = -self.ball_x
            self.velocity_x = -self.velocity_x
        if self.ball_y <= 0:     # hitting upper bound
            self.ball_y = -self.ball_y
            self.velocity_y = -self.velocity_y
        if self.ball_y  >= 1:    # hitting right bound
            self.ball_y = 2 - self.ball_y
            self.velocity_y = -self.velocity_y

In [16]:
def match(s):
    b_x = math.floor(s.ball_x * 12)
    b_y = math.floor(s.ball_y * 12)
    if s.velocity_x > 0:
        v_x = 1
    else:
        v_x = 0    # velocity_x <= 0 map to 0

    v_y = 0
    if s.velocity_y > 0 and abs(s.velocity_y) > 0.015:
        v_y = 1
    elif s.velocity_y < 0 and abs(s.velocity_y) > 0.015:    #velocity_y < 0.015 map to 2
        v_y = 2

    #print("paddle_y", s.paddle_y)
    p = math.floor(s.paddle_y / (1 - 0.2) * 12)
    if p == 12:
        p = 11
    #print("p", p)

    return (b_x ,b_y, v_x, v_y, p)

In [17]:
def reward(state):
    next_ball_x = state.ball_x + state.velocity_x

    if next_ball_x >= 1:        # hitting right bound
        if state.ball_y >= state.paddle_y and state.ball_y <= state.paddle_y + 0.2:    # hitting paddle
            return 0.5
        else:     # missing paddle
            return -1
        
    elif next_ball_x <= 0:
        if state.ball_y >= e.position and state.ball_y <= e.position + 0.2: 
            return -0.5
        else:
            return 1
    return 0

In [18]:
def max_Q(current_state):
    (b_x ,b_y, v_x, v_y, p) = match(get_up_test(current_state))
    Q_up = Q_table[b_x][b_y][v_x][v_y][p][0]
    
    (b_x ,b_y, v_x, v_y, p) = match(get_down_test(current_state))
    #print(b_x ,b_y, v_x, v_y, p)
    Q_down = Q_table[b_x][b_y][v_x][v_y][p][1]
    
    (b_x ,b_y, v_x, v_y, p) = match(get_no_move_test(current_state))
    Q_no_move = Q_table[b_x][b_y][v_x][v_y][p][2]
    
    #print(Q_up, Q_down, Q_no_move)
    
    return max(Q_up, Q_down, Q_no_move)

In [19]:
def argmax_f(current_state):
    (b_x ,b_y, v_x, v_y, p) = match(get_up_test(current_state))
    if N_sa[b_x][b_y][v_x][v_y][p][0] < N_e:
        f_up = 0
    else:
        f_up = Q_table[b_x][b_y][v_x][v_y][p][0]
    
    (b_x ,b_y, v_x, v_y, p) = match(get_down_test(current_state))
    if N_sa[b_x][b_y][v_x][v_y][p][1] < N_e:
        f_down = 0
    else:
        f_down = Q_table[b_x][b_y][v_x][v_y][p][1]
        
    (b_x ,b_y, v_x, v_y, p) = match(get_no_move_test(current_state))
    if N_sa[b_x][b_y][v_x][v_y][p][2] < N_e:
        f_no_move = 0
    else:
        f_no_move = Q_table[b_x][b_y][v_x][v_y][p][2]
    
    if f_up == f_down and f_down == f_no_move:
        return np.random.randint(3)
    
    return np.argmax([f_up, f_down, f_no_move])

In [20]:
def alpha(state):
    (b_x ,b_y, v_x, v_y, p) = match(state)
    num_visited = N_sa[b_x][b_y][v_x][v_y][p][a] 
    return 60 / (60 + num_visited)

In [21]:
Q_table = np.zeros((12, 12, 2, 3, 12, 3)) # x, y, v_x, v_y, paddle, action
Q_additional_state = -1                   # x >= 1 state
N_sa = np.zeros((12, 12, 2, 3, 12, 3))    # x, y, v_x, v_y, paddle, action

s = State(0,0,0,0,0)
s_empty = True
a = 0
r = 0

In [22]:
'''action: 0-up, 1-down, 2-no_move'''
def Q_agent(current_state, t):
    global s_empty
    global s
    global a
    global r
    global N_sa
    global Q
    if current_state.terminate:
        (b_x ,b_y, v_x, v_y, p) = match(s)
        #Q_table[b_x][b_y][v_x][v_y][p][3] = reward(current_state)

    if s_empty is False:
        # increment N_s
        (b_x ,b_y, v_x, v_y, p) = match(s)
        #print(b_x ,b_y, v_x, v_y, p, a)
        N_sa[b_x][b_y][v_x][v_y][p][a] += 1
        #print(N_sa[b_x][b_y][v_x][v_y][p][a])
        
        Q_table[b_x][b_y][v_x][v_y][p][a] =  Q_table[b_x][b_y][v_x][v_y][p][a] + \
                            alpha(s)* (r + gamma * max_Q(current_state) - Q_table[b_x][b_y][v_x][v_y][p][a])
        
    else:
        s_empty = False
    
    #s.empty = False
    s = copy.deepcopy(current_state)
    #print("s", match(s))
    
    (b_x ,b_y, v_x, v_y, p) = match(current_state)
    a = argmax_f(current_state)
    
    r = reward(current_state)
    
    return a

In [23]:
class enemy():
    position = 0.4
    height = 0.2
    speed = 0.02
    center = (position + height) / 2
    
    def __init__(self, pos):
        self.position = pos
        
    
    def up(self):
        self.position = max(self.position - self.speed, 0)
        #return self.position

    def down(self):
        self.position = min(self.position + self.speed, 0.8)
        #return self.position
    
    
    def getpos(self):
        return self.position
    
    

In [24]:
class Test_State(State):
    terminate_left = False
    terminate_right = False


    def update(self):
        global num_bounce
        global catch
        
        self.ball_x += self.velocity_x
        self.ball_y += self.velocity_y
        
        if self.ball_x >= 1:        # hitting right bound
            
            
            if self.ball_y >= self.paddle_y and self.ball_y <= self.paddle_y + 0.2:    # hitting paddle
                self.ball_x = 2 - self.ball_x
                #print("bounce")
                num_bounce += 1
#                 if curr_state not in state_tracker:
#                     #print(curr_state)
#                     state_tracker.append(curr_state)
                                
                self.velocity_x = -self.velocity_x + np.random.uniform(-0.015, 0.015)
                if self.velocity_x < 0:
                    self.velocity_x = min(-0.03, self.velocity_x)
                else:
                    self.velocity_x = max(0.03, self.velocity_x)
                if self.velocity_x > 1:
                    self.velocity_x = 1
                elif self.velocity_x < -1:
                    self.velocity_x = -1
                
                self.velocity_y += np.random.uniform(-0.03, 0.03)
                if self.velocity_y > 1:
                    self.velocity_y = 1
                elif self.velocity_y < -1:
                    self.velocity_y = -1
                    
                
                
            else:    # missing paddle
                self.ball_x =  2 - self.ball_x
#                 print("ai loss")
                self.terminate_right = True

            
        if self.ball_x <= 0:     # hitting left bound
#             print("neg x pos")
            if self.ball_y >= e.position and self.ball_y <= e.position + 0.2:    # hitting paddle
                self.ball_x = - self.ball_x

                catch += 1
                
                self.velocity_x = -self.velocity_x + np.random.uniform(-0.015, 0.015)
                if self.velocity_x < 0:
                    self.velocity_x = min(-0.03, self.velocity_x)
                else:
                    self.velocity_x = max(0.03, self.velocity_x)
                if self.velocity_x > 1:
                    self.velocity_x = 1
                elif self.velocity_x < -1:
                    self.velocity_x = -1
                
                self.velocity_y += np.random.uniform(-0.03, 0.03)
                if self.velocity_y > 1:
                    self.velocity_y = 1
                elif self.velocity_y < -1:
                    self.velocity_y = -1
            else:
                self.ball_x =  - self.ball_x
#                 print("enemy loss")
                self.terminate_left = True
                    
        if self.ball_y <= 0:     # hitting upper bound
            self.ball_y = -self.ball_y
            self.velocity_y = -self.velocity_y
        if self.ball_y  >= 1:    # hitting right bound
            self.ball_y = 2 - self.ball_y
            self.velocity_y = -self.velocity_y
        
        y_diff = self.ball_y - e.center

        if y_diff < 0:
            e.up()
        elif y_diff > 0:
            e.down()
        
        #print ("self.ball_x is: ", self.ball_x)
            

In [25]:

def get_up_test(current_state):
    #print("up current", match(current_state))
    new_state = Test_State(current_state.ball_x, current_state.ball_y, current_state.velocity_x, \
                      current_state.velocity_y, current_state.paddle_y)
    new_state.up()
    #print("new state", match(new_state))
    return new_state

def get_down_test(current_state):
    new_state = Test_State(current_state.ball_x, current_state.ball_y, current_state.velocity_x, \
                      current_state.velocity_y, current_state.paddle_y)
    new_state.down()
    return new_state

def get_no_move_test(current_state):
    new_state = Test_State(current_state.ball_x, current_state.ball_y, current_state.velocity_x, \
                      current_state.velocity_y, current_state.paddle_y)
    new_state.update()
    return new_state

In [26]:
t_ = 1
num_bounce = 0
total_num_bounce = 0

catch = 0

count_ai_win = 0
count_enemy_win = 0

for i in range(100000):
    s = Test_State(0.5, 0.5, 0.03, 0.01, 0.4)
    e = enemy(0.4)
    current_state = copy.deepcopy(s)
    print("round: ", i)
    num_bounce = 0
    catch = 0
    while s.terminate_left is False and s.terminate_right is False:
        
        next_action = Q_agent(current_state, t_)

        if next_action == 0:
            current_state.up()
        if next_action == 1:
            current_state.down()
        if next_action == 2:
            current_state.update()
        #print("current state", match(current_state))
    t_ += 1
    
    if (s.terminate_left): 
        
        print("AI win")
        count_ai_win += 1
    elif(s.terminate_right):
        print("enemy win")
        count_enemy_win += 1
    print("bounce:", num_bounce)
    total_num_bounce += num_bounce
    print("state visited: ",np.count_nonzero(Q_table))

round:  0
enemy win
bounce: 0
state visited:  1
round:  1
enemy win
bounce: 2
state visited:  3
round:  2
enemy win
bounce: 3
state visited:  7
round:  3
enemy win
bounce: 0
state visited:  8
round:  4
enemy win
bounce: 0
state visited:  9
round:  5
enemy win
bounce: 0
state visited:  10
round:  6
enemy win
bounce: 2
state visited:  10
round:  7
AI win
bounce: 3
state visited:  11
round:  8
enemy win
bounce: 0
state visited:  13
round:  9
enemy win
bounce: 2
state visited:  13
round:  10
enemy win
bounce: 0
state visited:  14
round:  11
enemy win
bounce: 0
state visited:  14
round:  12
enemy win
bounce: 3
state visited:  16
round:  13
enemy win
bounce: 0
state visited:  18
round:  14
enemy win
bounce: 4
state visited:  20
round:  15
enemy win
bounce: 0
state visited:  20
round:  16
enemy win
bounce: 0
state visited:  21
round:  17
AI win
bounce: 7
state visited:  26
round:  18
enemy win
bounce: 0
state visited:  26
round:  19
enemy win
bounce: 0
state visited:  27
round:  20
enemy win


AI win
bounce: 5
state visited:  253
round:  181
AI win
bounce: 7
state visited:  255
round:  182
AI win
bounce: 7
state visited:  256
round:  183
AI win
bounce: 12
state visited:  262
round:  184
AI win
bounce: 5
state visited:  269
round:  185
enemy win
bounce: 4
state visited:  269
round:  186
enemy win
bounce: 4
state visited:  269
round:  187
enemy win
bounce: 5
state visited:  273
round:  188
AI win
bounce: 12
state visited:  276
round:  189
AI win
bounce: 5
state visited:  277
round:  190
AI win
bounce: 5
state visited:  281
round:  191
AI win
bounce: 5
state visited:  282
round:  192
enemy win
bounce: 4
state visited:  282
round:  193
AI win
bounce: 5
state visited:  286
round:  194
enemy win
bounce: 12
state visited:  293
round:  195
enemy win
bounce: 12
state visited:  298
round:  196
AI win
bounce: 5
state visited:  300
round:  197
enemy win
bounce: 4
state visited:  300
round:  198
AI win
bounce: 5
state visited:  303
round:  199
AI win
bounce: 7
state visited:  306
round: 

AI win
bounce: 7
state visited:  1005
round:  354
AI win
bounce: 5
state visited:  1010
round:  355
AI win
bounce: 5
state visited:  1015
round:  356
AI win
bounce: 5
state visited:  1018
round:  357
AI win
bounce: 5
state visited:  1019
round:  358
AI win
bounce: 7
state visited:  1021
round:  359
AI win
bounce: 7
state visited:  1026
round:  360
AI win
bounce: 7
state visited:  1037
round:  361
enemy win
bounce: 7
state visited:  1040
round:  362
enemy win
bounce: 12
state visited:  1044
round:  363
AI win
bounce: 7
state visited:  1051
round:  364
enemy win
bounce: 7
state visited:  1056
round:  365
AI win
bounce: 7
state visited:  1058
round:  366
enemy win
bounce: 13
state visited:  1062
round:  367
enemy win
bounce: 7
state visited:  1068
round:  368
AI win
bounce: 7
state visited:  1072
round:  369
AI win
bounce: 7
state visited:  1080
round:  370
AI win
bounce: 5
state visited:  1091
round:  371
AI win
bounce: 5
state visited:  1098
round:  372
AI win
bounce: 7
state visited:  

AI win
bounce: 7
state visited:  1969
round:  517
AI win
bounce: 5
state visited:  1976
round:  518
enemy win
bounce: 7
state visited:  1981
round:  519
enemy win
bounce: 5
state visited:  1985
round:  520
AI win
bounce: 5
state visited:  1995
round:  521
AI win
bounce: 7
state visited:  1996
round:  522
enemy win
bounce: 5
state visited:  2005
round:  523
enemy win
bounce: 5
state visited:  2008
round:  524
AI win
bounce: 7
state visited:  2013
round:  525
AI win
bounce: 5
state visited:  2018
round:  526
AI win
bounce: 5
state visited:  2020
round:  527
AI win
bounce: 7
state visited:  2027
round:  528
AI win
bounce: 7
state visited:  2034
round:  529
AI win
bounce: 7
state visited:  2036
round:  530
enemy win
bounce: 7
state visited:  2043
round:  531
AI win
bounce: 5
state visited:  2047
round:  532
AI win
bounce: 5
state visited:  2059
round:  533
AI win
bounce: 7
state visited:  2064
round:  534
enemy win
bounce: 11
state visited:  2068
round:  535
AI win
bounce: 5
state visited:

AI win
bounce: 5
state visited:  2785
round:  701
AI win
bounce: 7
state visited:  2791
round:  702
enemy win
bounce: 5
state visited:  2793
round:  703
AI win
bounce: 5
state visited:  2793
round:  704
enemy win
bounce: 5
state visited:  2794
round:  705
AI win
bounce: 7
state visited:  2794
round:  706
AI win
bounce: 7
state visited:  2798
round:  707
AI win
bounce: 7
state visited:  2798
round:  708
AI win
bounce: 7
state visited:  2801
round:  709
AI win
bounce: 7
state visited:  2801
round:  710
AI win
bounce: 5
state visited:  2802
round:  711
AI win
bounce: 5
state visited:  2802
round:  712
AI win
bounce: 7
state visited:  2803
round:  713
enemy win
bounce: 7
state visited:  2807
round:  714
AI win
bounce: 7
state visited:  2808
round:  715
enemy win
bounce: 7
state visited:  2816
round:  716
AI win
bounce: 5
state visited:  2818
round:  717
AI win
bounce: 7
state visited:  2819
round:  718
AI win
bounce: 5
state visited:  2820
round:  719
enemy win
bounce: 7
state visited:  28

...

AI win
bounce: 7
state visited:  26691
round:  99224
AI win
bounce: 14
state visited:  26691
round:  99225
AI win
bounce: 7
state visited:  26691
round:  99226
AI win
bounce: 14
state visited:  26691
round:  99227
AI win
bounce: 8
state visited:  26691
round:  99228
AI win
bounce: 7
state visited:  26691
round:  99229
enemy win
bounce: 7
state visited:  26691
round:  99230
AI win
bounce: 7
state visited:  26691
round:  99231
AI win
bounce: 7
state visited:  26691
round:  99232
AI win
bounce: 12
state visited:  26691
round:  99233
enemy win
bounce: 7
state visited:  26691
round:  99234
AI win
bounce: 7
state visited:  26691
round:  99235
AI win
bounce: 17
state visited:  26691
round:  99236
AI win
bounce: 5
state visited:  26691
round:  99237
enemy win
bounce: 7
state visited:  26691
round:  99238
AI win
bounce: 7
state visited:  26691
round:  99239
AI win
bounce: 7
state visited:  26691
round:  99240
AI win
bounce: 15
state visited:  26691
round:  99241
AI win
bounce: 10
state visited:

AI win
bounce: 15
state visited:  26693
round:  99380
AI win
bounce: 14
state visited:  26693
round:  99381
AI win
bounce: 7
state visited:  26693
round:  99382
AI win
bounce: 7
state visited:  26693
round:  99383
AI win
bounce: 5
state visited:  26693
round:  99384
AI win
bounce: 17
state visited:  26693
round:  99385
AI win
bounce: 7
state visited:  26693
round:  99386
AI win
bounce: 7
state visited:  26693
round:  99387
AI win
bounce: 5
state visited:  26693
round:  99388
AI win
bounce: 7
state visited:  26693
round:  99389
AI win
bounce: 7
state visited:  26693
round:  99390
AI win
bounce: 7
state visited:  26693
round:  99391
AI win
bounce: 7
state visited:  26693
round:  99392
AI win
bounce: 10
state visited:  26693
round:  99393
AI win
bounce: 7
state visited:  26693
round:  99394
AI win
bounce: 28
state visited:  26693
round:  99395
AI win
bounce: 7
state visited:  26693
round:  99396
AI win
bounce: 7
state visited:  26693
round:  99397
AI win
bounce: 5
state visited:  26693
ro

enemy win
bounce: 14
state visited:  26693
round:  99535
AI win
bounce: 7
state visited:  26693
round:  99536
AI win
bounce: 7
state visited:  26693
round:  99537
AI win
bounce: 5
state visited:  26693
round:  99538
AI win
bounce: 7
state visited:  26693
round:  99539
AI win
bounce: 29
state visited:  26693
round:  99540
AI win
bounce: 7
state visited:  26693
round:  99541
AI win
bounce: 5
state visited:  26693
round:  99542
AI win
bounce: 7
state visited:  26693
round:  99543
enemy win
bounce: 14
state visited:  26693
round:  99544
AI win
bounce: 19
state visited:  26693
round:  99545
AI win
bounce: 7
state visited:  26693
round:  99546
AI win
bounce: 8
state visited:  26693
round:  99547
AI win
bounce: 7
state visited:  26693
round:  99548
AI win
bounce: 7
state visited:  26693
round:  99549
AI win
bounce: 7
state visited:  26693
round:  99550
AI win
bounce: 7
state visited:  26693
round:  99551
enemy win
bounce: 5
state visited:  26693
round:  99552
AI win
bounce: 7
state visited:  

AI win
bounce: 7
state visited:  26699
round:  99710
enemy win
bounce: 21
state visited:  26699
round:  99711
AI win
bounce: 7
state visited:  26699
round:  99712
AI win
bounce: 5
state visited:  26699
round:  99713
AI win
bounce: 7
state visited:  26699
round:  99714
AI win
bounce: 7
state visited:  26699
round:  99715
AI win
bounce: 7
state visited:  26699
round:  99716
enemy win
bounce: 14
state visited:  26699
round:  99717
AI win
bounce: 5
state visited:  26699
round:  99718
enemy win
bounce: 26
state visited:  26699
round:  99719
AI win
bounce: 7
state visited:  26699
round:  99720
AI win
bounce: 12
state visited:  26699
round:  99721
AI win
bounce: 5
state visited:  26699
round:  99722
AI win
bounce: 28
state visited:  26699
round:  99723
AI win
bounce: 7
state visited:  26699
round:  99724
enemy win
bounce: 7
state visited:  26699
round:  99725
AI win
bounce: 7
state visited:  26699
round:  99726
AI win
bounce: 15
state visited:  26699
round:  99727
AI win
bounce: 7
state visit

AI win
bounce: 7
state visited:  26699
round:  99876
AI win
bounce: 7
state visited:  26699
round:  99877
AI win
bounce: 7
state visited:  26699
round:  99878
AI win
bounce: 7
state visited:  26699
round:  99879
AI win
bounce: 31
state visited:  26699
round:  99880
enemy win
bounce: 12
state visited:  26699
round:  99881
AI win
bounce: 7
state visited:  26699
round:  99882
AI win
bounce: 7
state visited:  26699
round:  99883
AI win
bounce: 26
state visited:  26699
round:  99884
AI win
bounce: 8
state visited:  26699
round:  99885
AI win
bounce: 7
state visited:  26699
round:  99886
AI win
bounce: 7
state visited:  26699
round:  99887
AI win
bounce: 7
state visited:  26699
round:  99888
AI win
bounce: 5
state visited:  26699
round:  99889
AI win
bounce: 7
state visited:  26699
round:  99890
AI win
bounce: 7
state visited:  26699
round:  99891
AI win
bounce: 14
state visited:  26699
round:  99892
AI win
bounce: 7
state visited:  26699
round:  99893
AI win
bounce: 5
state visited:  26699


In [27]:
print("average bouncing per game: ", total_num_bounce / 100000)

print("totoal state visited after training: ", np.count_nonzero(Q_table))

average bouncing per game:  8.27481
totoal state visited after training:  26699


In [28]:
print("ai win times is: ", count_ai_win)
print("enemy win times is: ", count_enemy_win)


ai win times is:  81845
enemy win times is:  18155


In [29]:
print("ai winning rate is: ", count_ai_win / 100000)

ai winning rate is:  0.81845


In [34]:
def Q_agent_test(current_state, t):
    global s_empty
    global s
    global a
    global r
    global N_sa
    global Q


    if s_empty is False:
        # increment N_s
        (b_x ,b_y, v_x, v_y, p) = match(s)
        
    else:
        s_empty = False
    
    #s.empty = False
    s = copy.deepcopy(current_state)
    #print("s", match(s))
    
    (b_x ,b_y, v_x, v_y, p) = match(current_state)
    a = argmax_f_test(current_state)
    
    r = reward(current_state)
    
    return a

In [35]:
def argmax_f_test(current_state):
    (b_x ,b_y, v_x, v_y, p) = match(get_up_test(current_state))
    #print ('up' , (b_x ,b_y, v_x, v_y, p))
    f_up = Q_table[b_x][b_y][v_x][v_y][p][0]
    
    (b_x ,b_y, v_x, v_y, p) = match(get_down_test(current_state))
    #print ('down', (b_x ,b_y, v_x, v_y, p))

    f_down = Q_table[b_x][b_y][v_x][v_y][p][1]
        
    (b_x ,b_y, v_x, v_y, p) = match(get_no_move_test(current_state))
    #print ('nothing',(b_x ,b_y, v_x, v_y, p))

    f_no_move = Q_table[b_x][b_y][v_x][v_y][p][2]
    
    if f_up == f_down and f_down == f_no_move:
        return np.random.randint(3)
    
    return np.argmax([f_up, f_down, f_no_move])

In [36]:
t_ = 1
num_bounce = 0
total_num_bounce = 0

catch = 0

count_ai_win = 0
count_enemy_win = 0

for i in range(1000):
    s = Test_State(0.5, 0.5, 0.03, 0.01, 0.4)
    e = enemy(0.4)
    current_state = copy.deepcopy(s)
    print("round: ", i)
    num_bounce = 0
    catch = 0
    while s.terminate_left is False and s.terminate_right is False:
        
        next_action = Q_agent_test(current_state, t_)

        if next_action == 0:
            current_state.up()
        if next_action == 1:
            current_state.down()
        if next_action == 2:
            current_state.update()
        #print("current state", match(current_state))
    t_ += 1
    
    if (s.terminate_left): 
        
        print("AI win")
        count_ai_win += 1
    elif(s.terminate_right):
        print("enemy win")
        count_enemy_win += 1
    print("bounce:", num_bounce)
    total_num_bounce += num_bounce
    print("state visited: ",np.count_nonzero(Q_table))


round:  0
AI win
bounce: 4
state visited:  26699
round:  1
AI win
bounce: 4
state visited:  26699
round:  2
AI win
bounce: 6
state visited:  26699
round:  3
AI win
bounce: 4
state visited:  26699
round:  4
enemy win
bounce: 7
state visited:  26699
round:  5
AI win
bounce: 4
state visited:  26699
round:  6
AI win
bounce: 4
state visited:  26699
round:  7
AI win
bounce: 4
state visited:  26699
round:  8
AI win
bounce: 8
state visited:  26699
round:  9
AI win
bounce: 4
state visited:  26699
round:  10
enemy win
bounce: 4
state visited:  26699
round:  11
AI win
bounce: 4
state visited:  26699
round:  12
AI win
bounce: 4
state visited:  26699
round:  13
AI win
bounce: 4
state visited:  26699
round:  14
enemy win
bounce: 7
state visited:  26699
round:  15
AI win
bounce: 8
state visited:  26699
round:  16
AI win
bounce: 4
state visited:  26699
round:  17
AI win
bounce: 4
state visited:  26699
round:  18
AI win
bounce: 4
state visited:  26699
round:  19
AI win
bounce: 4
state visited:  26699
r

AI win
bounce: 4
state visited:  26699
round:  198
AI win
bounce: 4
state visited:  26699
round:  199
enemy win
bounce: 8
state visited:  26699
round:  200
enemy win
bounce: 11
state visited:  26699
round:  201
AI win
bounce: 4
state visited:  26699
round:  202
AI win
bounce: 4
state visited:  26699
round:  203
enemy win
bounce: 18
state visited:  26699
round:  204
AI win
bounce: 4
state visited:  26699
round:  205
AI win
bounce: 4
state visited:  26699
round:  206
AI win
bounce: 4
state visited:  26699
round:  207
AI win
bounce: 4
state visited:  26699
round:  208
AI win
bounce: 4
state visited:  26699
round:  209
AI win
bounce: 4
state visited:  26699
round:  210
AI win
bounce: 6
state visited:  26699
round:  211
AI win
bounce: 4
state visited:  26699
round:  212
AI win
bounce: 4
state visited:  26699
round:  213
AI win
bounce: 4
state visited:  26699
round:  214
AI win
bounce: 4
state visited:  26699
round:  215
AI win
bounce: 8
state visited:  26699
round:  216
AI win
bounce: 4
sta

AI win
bounce: 12
state visited:  26699
round:  366
AI win
bounce: 4
state visited:  26699
round:  367
AI win
bounce: 4
state visited:  26699
round:  368
AI win
bounce: 4
state visited:  26699
round:  369
enemy win
bounce: 8
state visited:  26699
round:  370
AI win
bounce: 8
state visited:  26699
round:  371
AI win
bounce: 4
state visited:  26699
round:  372
AI win
bounce: 4
state visited:  26699
round:  373
AI win
bounce: 4
state visited:  26699
round:  374
AI win
bounce: 4
state visited:  26699
round:  375
AI win
bounce: 11
state visited:  26699
round:  376
AI win
bounce: 4
state visited:  26699
round:  377
enemy win
bounce: 7
state visited:  26699
round:  378
AI win
bounce: 4
state visited:  26699
round:  379
AI win
bounce: 4
state visited:  26699
round:  380
AI win
bounce: 4
state visited:  26699
round:  381
AI win
bounce: 4
state visited:  26699
round:  382
AI win
bounce: 4
state visited:  26699
round:  383
AI win
bounce: 7
state visited:  26699
round:  384
enemy win
bounce: 8
sta

AI win
bounce: 4
state visited:  26699
round:  535
AI win
bounce: 4
state visited:  26699
round:  536
AI win
bounce: 10
state visited:  26699
round:  537
AI win
bounce: 4
state visited:  26699
round:  538
AI win
bounce: 4
state visited:  26699
round:  539
AI win
bounce: 8
state visited:  26699
round:  540
AI win
bounce: 4
state visited:  26699
round:  541
AI win
bounce: 12
state visited:  26699
round:  542
AI win
bounce: 4
state visited:  26699
round:  543
AI win
bounce: 4
state visited:  26699
round:  544
AI win
bounce: 4
state visited:  26699
round:  545
AI win
bounce: 6
state visited:  26699
round:  546
AI win
bounce: 4
state visited:  26699
round:  547
enemy win
bounce: 6
state visited:  26699
round:  548
AI win
bounce: 4
state visited:  26699
round:  549
AI win
bounce: 4
state visited:  26699
round:  550
AI win
bounce: 4
state visited:  26699
round:  551
enemy win
bounce: 8
state visited:  26699
round:  552
AI win
bounce: 12
state visited:  26699
round:  553
AI win
bounce: 4
state

AI win
bounce: 4
state visited:  26699
round:  701
AI win
bounce: 4
state visited:  26699
round:  702
AI win
bounce: 4
state visited:  26699
round:  703
enemy win
bounce: 4
state visited:  26699
round:  704
AI win
bounce: 4
state visited:  26699
round:  705
AI win
bounce: 4
state visited:  26699
round:  706
AI win
bounce: 4
state visited:  26699
round:  707
AI win
bounce: 4
state visited:  26699
round:  708
AI win
bounce: 4
state visited:  26699
round:  709
AI win
bounce: 4
state visited:  26699
round:  710
AI win
bounce: 8
state visited:  26699
round:  711
AI win
bounce: 4
state visited:  26699
round:  712
enemy win
bounce: 10
state visited:  26699
round:  713
AI win
bounce: 4
state visited:  26699
round:  714
AI win
bounce: 4
state visited:  26699
round:  715
AI win
bounce: 8
state visited:  26699
round:  716
AI win
bounce: 4
state visited:  26699
round:  717
enemy win
bounce: 5
state visited:  26699
round:  718
AI win
bounce: 4
state visited:  26699
round:  719
AI win
bounce: 12
sta

enemy win
bounce: 4
state visited:  26699
round:  876
AI win
bounce: 8
state visited:  26699
round:  877
enemy win
bounce: 4
state visited:  26699
round:  878
AI win
bounce: 4
state visited:  26699
round:  879
AI win
bounce: 4
state visited:  26699
round:  880
enemy win
bounce: 4
state visited:  26699
round:  881
AI win
bounce: 4
state visited:  26699
round:  882
AI win
bounce: 4
state visited:  26699
round:  883
AI win
bounce: 4
state visited:  26699
round:  884
AI win
bounce: 4
state visited:  26699
round:  885
AI win
bounce: 4
state visited:  26699
round:  886
AI win
bounce: 4
state visited:  26699
round:  887
AI win
bounce: 10
state visited:  26699
round:  888
AI win
bounce: 4
state visited:  26699
round:  889
AI win
bounce: 4
state visited:  26699
round:  890
AI win
bounce: 4
state visited:  26699
round:  891
AI win
bounce: 8
state visited:  26699
round:  892
AI win
bounce: 4
state visited:  26699
round:  893
AI win
bounce: 8
state visited:  26699
round:  894
AI win
bounce: 4
stat

In [38]:
print("average bouncing per game: ", total_num_bounce / 1000)

print("totoal state visited after training: ", np.count_nonzero(Q_table))

average bouncing per game:  5.054
totoal state visited after training:  26699


In [39]:
print("ai win times is: ", count_ai_win)
print("enemy win times is: ", count_enemy_win)


ai win times is:  879
enemy win times is:  121


In [40]:
print("ai winning rate is: ", count_ai_win / 1000)

ai winning rate is:  0.879
